## Compare different models
### Load data 

In [21]:
import pandas as pd
from matplotlib import pyplot
import matplotlib.pyplot as plt
import numpy as np
import random
from operator import itemgetter
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import Imputer
from sklearn.metrics import mean_squared_error
from collections import Counter
from collections import defaultdict
%matplotlib inline

In [2]:
# Load Train data 
df_train_prepared = pd.read_pickle('df_train_prepared')

train_payprice = df_train_prepared['payprice']
train_bidprice = df_train_prepared['bidprice']

df_train = df_train_prepared.drop(['payprice','bidprice'], axis =1)
df_train.head()

# Scale train data 
standard_scaler = StandardScaler().fit(df_train)
train_x = standard_scaler.transform(df_train)
train_x[:1]

array([[-0.02716812,  1.02735543,  1.2959677 , -1.44404095, -1.47450021,
        -0.07241839, -1.17330636,  0.08690655, -0.58626423,  0.74759644,
         0.34754529, -0.02093817, -0.53713615,  1.42983954, -1.79876415,
        -0.03051079, -0.74630917,  0.83640481, -1.64992635,  1.21503638]])

In [7]:
# CTR for train data 
train_click_1 = df_train[df_train['click'] == 1]
train_AvgCTR = len(train_click_1)/len(df_train['click'])
print('Train CTR:',train_AvgCTR)

Train CTR: 0.0007375623256619447


In [4]:
# Load Validation data 
df_val_prepared = pd.read_pickle('df_val_prepared')

val_payprice = df_val_prepared['payprice']
val_bidprice = df_val_prepared['bidprice']
val_click = df_val_prepared['click']
df_val = df_val_prepared.drop(['payprice','bidprice'], axis =1)
df_val.head()

# Scale validation data 
standard_scaler = StandardScaler().fit(df_val)
val_x = standard_scaler.transform(df_val)
val_x[:1]

array([[-0.02578914,  0.54310061,  0.98980048, -0.68871428, -0.72819482,
        -1.16598138, -1.30074929,  3.12709522, -0.72222819, -1.75178669,
         0.35195772,  0.67377474, -0.60695559,  1.33457283,  0.58957062,
        -0.02894579,  0.11112068,  1.01082565,  0.28468824,  1.09400445]])

In [6]:
# CTR for validation data 
val_click_1 = df_val_prepared[df_val_prepared['click'] == 1]
val_AvgCTR = float("{0:.5f}".format(len(val_click_1)/len(val_click)))
print('Validation CTR:',val_AvgCTR)


Validation CTR: 0.00066


## Linear Prediction 

bid = basebid x pCTR/avgCTR

- Guys, please come up with different ways of calculate base bid so we can compare
- I use mean and standard deviant / 1000  as base bid

In [9]:
df_tree_pred = pd.read_pickle('df_tree_prediction')
df_tree_pred['probability_1_click'] 
linear_bid = []

# Standard Deviation of Bid Price 

std = np.std(val_bidprice)/1000


base= val_bidprice.mean()/1000 + (3*std )
base = float("{0:.2f}".format(base))
 

for pCTR in df_tree_pred['probability_1_click']:
    bid = float("{0:.2f}".format(base * pCTR/val_AvgCTR ))
    linear_bid.append(bid)


### Prediction bidprice, payprice with Linear Regression

- Machine Learning Linear Regression to predict price
- This bids on every bids, has not taken CTR into decision to bid or not
- I plan to do that later 


In [10]:
# Function for calculating mean square root error 
# To measure the accuray of the predicion 

def calculate_rmse (test_y, pred_y, model_name):
    mse = mean_squared_error(test_y, pred_y)
    rmse = np.sqrt(mse)
    print('rmse for', model_name, rmse )
    

In [11]:
from sklearn.linear_model import LinearRegression 

linear_reg = LinearRegression() 
linear_reg.fit(train_x ,train_bidprice)

lin_pred_bid = linear_reg.predict(val_x) 
lin_pred_bid

/Users/hd/ml/env/lib/python3.6/site-packages/scipy/linalg/basic.py:1226: RuntimeWarning: internal gelsd driver lwork query error, required iwork dimension not returned. This is likely the result of LAPACK bug 0038, fixed in LAPACK 3.2.2 (released July 21, 2010). Falling back to 'gelss' driver.
  warnings.warn(mesg, RuntimeWarning)


array([290.59537147, 248.2801378 , 237.75047116, ..., 270.86430107,
       288.96457353, 264.72962324])

In [12]:
calculate_rmse(val_bidprice, lin_pred_bid, 'linear regression')

rmse for linear regression 18.960065580808298


### Random Bidding 

- I just choose random bids from all the previous bid price


In [13]:
def get_sample(arr, size, fast=True):
    samplesize = size
    return np.random.choice(arr, size, replace=False)

random = get_sample(val_bidprice,len(val_bidprice))
random

array([300, 238, 294, ..., 241, 300, 300])

In [14]:
calculate_rmse(val_bidprice, random, 'random')

rmse for random 40.85861602219484


## Evaluate the three models

In [15]:
# Function to combine model names and price 
def model_nvalue(key, value):
    test_bid_ls = []
    if type(value) != list:
        value_list = value.tolist()
        for i in value_list:
            test_bid = ((key),i)
            test_bid_ls.append(test_bid)
    
    else:
        for i in value:
            test_bid = ((key),i)
            test_bid_ls.append(test_bid)
    return test_bid_ls

In [16]:
# Function to choose win bid from 3 models
result_ls = []

def win_bid(click, model1, model2, model3):
    budget_m2 = 6250 
    budget_m3 = 6250 
    for i in range(len(model1)):
        if budget_m2 > model2[i][1] and budget_m3 > model3[i][1]:
            all_bid = (model1[i], model2[i], model3[i])
        
        elif budget_m2 < model2[i][1]  and budget_m3 > model3[i][1]:
            all_bid = (model1[i], (model2[i][0], 0), model3[i])
            print('Budget Spent for model 2')
        
        elif budget_m2 > model2[i][1] and budget_m3 < model3[i][1]:
            all_bid = (model1[i], model2[i], (model3[i][0], 0))
            print('Budget Spent for model 3')
            
        elif budget_m2 < model2[i][1] and budget_m3 < model3[i][1]:
            print('Budget Spent for model 2 and 3')
            return result_ls
        
        all_bid = sorted(all_bid, key = lambda x:x[1], reverse = True)
        
        wbid= {}
        k =  all_bid[0][0]
        wbid[k] = all_bid[0][1]
        
        
        s_price = all_bid[1][1]
        wbid['zsecond payprice'] = s_price
        wbid['click'] = click[i]
        result_ls.append(wbid)
        print(i, wbid)
        
        
        if k == model2[0][0]:
            budget_m2 = budget_m2 - s_price/1000
            #print('Model 2 Wins! Budget m2 remaining:', budget_m2, "Budget m3 remaining:", budget_m3)
            print()
        elif k == model3[0][0]:
            budget_m3 = budget_m3 - s_price/1000
            #print('Model 3 Wins! Budget m2 remaining:', budget_m2, "Budget m3 remaining:", budget_m3)
            print()
        else:
            #print('Model 1 Wins! Budget m2 remaining:', budget_m2, "Budget m3 remaining:", budget_m3)
            print()
       
    return result_ls

In [17]:
# Convert bidprice to tuple for using in function above
val_click_ls  = val_click.tolist()
val_bids = model_nvalue('validation_bid',val_bidprice)

linearreg_bids = model_nvalue('lin_reg',lin_pred_bid.astype(int))

random_bids = model_nvalue('random', random)

linear_bids = model_nvalue('linear',linear_bid )

In [18]:
# Compare the three models: val_bids, random_bids, linear_bids
# This takes a while to run 

test = win_bid(val_click_ls,val_bids,random_bids,linear_bids)
test 

0 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

1 {'validation_bid': 238, 'zsecond payprice': 238, 'click': 0}

2 {'random': 294, 'zsecond payprice': 238, 'click': 0}

3 {'validation_bid': 238, 'zsecond payprice': 238, 'click': 0}

4 {'random': 300, 'zsecond payprice': 249, 'click': 0}

5 {'random': 294, 'zsecond payprice': 241, 'click': 0}

6 {'random': 300, 'zsecond payprice': 227, 'click': 0}

7 {'random': 238, 'zsecond payprice': 227, 'click': 0}

8 {'validation_bid': 249, 'zsecond payprice': 238, 'click': 0}

9 {'validation_bid': 241, 'zsecond payprice': 241, 'click': 0}

10 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

11 {'random': 300, 'zsecond payprice': 241, 'click': 0}

12 {'random': 249, 'zsecond payprice': 238, 'click': 0}

13 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

14 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

15 {'validation_bid': 300, 'zsecond payprice': 238, 'click': 0}

16 {'validation_bid': 300, 'zsecond 

530 {'random': 300, 'zsecond payprice': 238, 'click': 0}

531 {'validation_bid': 300, 'zsecond payprice': 294, 'click': 0}

532 {'random': 300, 'zsecond payprice': 238, 'click': 0}

533 {'validation_bid': 294, 'zsecond payprice': 277, 'click': 0}

534 {'validation_bid': 300, 'zsecond payprice': 277, 'click': 0}

535 {'validation_bid': 300, 'zsecond payprice': 254, 'click': 0}

536 {'random': 294, 'zsecond payprice': 238, 'click': 0}

537 {'validation_bid': 300, 'zsecond payprice': 241, 'click': 0}

538 {'random': 300, 'zsecond payprice': 294, 'click': 0}

539 {'random': 300, 'zsecond payprice': 294, 'click': 0}

540 {'linear': 308.27, 'zsecond payprice': 241, 'click': 0}

541 {'validation_bid': 300, 'zsecond payprice': 227, 'click': 0}

542 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

543 {'random': 294, 'zsecond payprice': 249, 'click': 0}

544 {'validation_bid': 300, 'zsecond payprice': 294, 'click': 0}

545 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

54


1235 {'validation_bid': 300, 'zsecond payprice': 294, 'click': 0}

1236 {'random': 294, 'zsecond payprice': 238, 'click': 0}

1237 {'random': 300, 'zsecond payprice': 227, 'click': 0}

1238 {'random': 300, 'zsecond payprice': 238, 'click': 0}

1239 {'validation_bid': 300, 'zsecond payprice': 277, 'click': 0}

1240 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

1241 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

1242 {'linear': 319.29, 'zsecond payprice': 300, 'click': 0}

1243 {'random': 300, 'zsecond payprice': 227, 'click': 0}

1244 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

1245 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

1246 {'random': 300, 'zsecond payprice': 294, 'click': 0}

1247 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

1248 {'validation_bid': 300, 'zsecond payprice': 241, 'click': 0}

1249 {'validation_bid': 300, 'zsecond payprice': 238, 'click': 0}

1250 {'validation_bid': 300, 'zsecond payprice': 238, 


1867 {'random': 294, 'zsecond payprice': 238, 'click': 0}

1868 {'linear': 308.27, 'zsecond payprice': 294, 'click': 0}

1869 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

1870 {'random': 294, 'zsecond payprice': 249, 'click': 0}

1871 {'validation_bid': 227, 'zsecond payprice': 227, 'click': 0}

1872 {'validation_bid': 294, 'zsecond payprice': 277, 'click': 0}

1873 {'validation_bid': 294, 'zsecond payprice': 249, 'click': 0}

1874 {'linear': 308.27, 'zsecond payprice': 277, 'click': 0}

1875 {'random': 300, 'zsecond payprice': 227, 'click': 0}

1876 {'validation_bid': 300, 'zsecond payprice': 241, 'click': 0}

1877 {'linear': 319.29, 'zsecond payprice': 300, 'click': 0}

1878 {'random': 277, 'zsecond payprice': 238, 'click': 0}

1879 {'validation_bid': 277, 'zsecond payprice': 254, 'click': 0}

1880 {'validation_bid': 294, 'zsecond payprice': 227, 'click': 0}

1881 {'validation_bid': 238, 'zsecond payprice': 227, 'click': 0}

1882 {'linear': 308.27, 'zsecond payprice

2439 {'validation_bid': 294, 'zsecond payprice': 294, 'click': 0}

2440 {'validation_bid': 277, 'zsecond payprice': 238, 'click': 0}

2441 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

2442 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

2443 {'random': 238, 'zsecond payprice': 227, 'click': 0}

2444 {'validation_bid': 300, 'zsecond payprice': 294, 'click': 0}

2445 {'validation_bid': 300, 'zsecond payprice': 294, 'click': 0}

2446 {'random': 300, 'zsecond payprice': 227, 'click': 0}

2447 {'linear': 308.27, 'zsecond payprice': 277, 'click': 0}

2448 {'random': 294, 'zsecond payprice': 238, 'click': 0}

2449 {'validation_bid': 249, 'zsecond payprice': 241, 'click': 0}

2450 {'linear': 319.29, 'zsecond payprice': 254, 'click': 0}

2451 {'validation_bid': 300, 'zsecond payprice': 249, 'click': 0}

2452 {'random': 300, 'zsecond payprice': 227, 'click': 0}

2453 {'validation_bid': 300, 'zsecond payprice': 300, 'click': 0}

2454 {'validation_bid': 300, 'zsecond payp

...

80400 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

80401 {'validation_bid': 238, 'zsecond payprice': 238, 'click': 0}

Budget Spent for model 2
80402 {'linear': 308.27, 'zsecond payprice': 277, 'click': 0}

Budget Spent for model 2
80403 {'validation_bid': 294, 'zsecond payprice': 210.85, 'click': 0}

80404 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

Budget Spent for model 2
80405 {'validation_bid': 238, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
80406 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
80407 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

80408 {'validation_bid': 300, 'zsecond payprice': 241, 'click': 0}

Budget Spent for model 2
80409 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

80410 {'validation_bid': 294, 'zsecond payprice': 227, 'click': 0}

Budget Spent for model 2
80411 {'validation_bid': 277, 'zsecond payprice': 210.85, 'click': 0}

Budget


80780 {'linear': 308.27, 'zsecond payprice': 254, 'click': 0}

Budget Spent for model 2
80781 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

80782 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

80783 {'validation_bid': 294, 'zsecond payprice': 238, 'click': 0}

80784 {'validation_bid': 277, 'zsecond payprice': 227, 'click': 0}

Budget Spent for model 2
80785 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

Budget Spent for model 2
80786 {'validation_bid': 227, 'zsecond payprice': 210.85, 'click': 0}

80787 {'validation_bid': 238, 'zsecond payprice': 238, 'click': 0}

80788 {'validation_bid': 300, 'zsecond payprice': 238, 'click': 0}

Budget Spent for model 2
80789 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

80790 {'linear': 490.54, 'zsecond payprice': 277, 'click': 0}

Budget Spent for model 2
80791 {'validation_bid': 277, 'zsecond payprice': 210.85, 'click': 0}

80792 {'validation_bid': 249, 'zsecond payprice': 227, 'click': 0}

Budget

Budget Spent for model 2
81143 {'validation_bid': 227, 'zsecond payprice': 210.85, 'click': 0}

81144 {'validation_bid': 300, 'zsecond payprice': 227, 'click': 0}

Budget Spent for model 2
81145 {'validation_bid': 254, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81146 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81147 {'validation_bid': 241, 'zsecond payprice': 210.85, 'click': 0}

81148 {'random': 254, 'zsecond payprice': 249, 'click': 0}

Budget Spent for model 2
81149 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81150 {'linear': 490.54, 'zsecond payprice': 300, 'click': 0}

Budget Spent for model 2
81151 {'validation_bid': 300, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81152 {'validation_bid': 227, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81153 {'validation_bid': 238, 'zsecond payprice': 210.85, 'click': 0}

81154 {'validati


81532 {'validation_bid': 300, 'zsecond payprice': 241, 'click': 0}

81533 {'validation_bid': 241, 'zsecond payprice': 238, 'click': 0}

Budget Spent for model 2
81534 {'validation_bid': 241, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81535 {'validation_bid': 238, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81536 {'linear': 490.54, 'zsecond payprice': 227, 'click': 0}

81537 {'linear': 308.27, 'zsecond payprice': 254, 'click': 0}

Budget Spent for model 2
81538 {'validation_bid': 294, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81539 {'validation_bid': 277, 'zsecond payprice': 210.85, 'click': 0}

Budget Spent for model 2
81540 {'linear': 308.27, 'zsecond payprice': 300, 'click': 0}

Budget Spent for model 2
81541 {'validation_bid': 238, 'zsecond payprice': 210.85, 'click': 0}

81542 {'linear': 490.54, 'zsecond payprice': 241, 'click': 0}

Budget Spent for model 2
81543 {'validation_bid': 300, 'zsecond payprice': 210.85

[{'click': 0, 'validation_bid': 300, 'zsecond payprice': 300},
 {'click': 0, 'validation_bid': 238, 'zsecond payprice': 238},
 {'click': 0, 'random': 294, 'zsecond payprice': 238},
 {'click': 0, 'validation_bid': 238, 'zsecond payprice': 238},
 {'click': 0, 'random': 300, 'zsecond payprice': 249},
 {'click': 0, 'random': 294, 'zsecond payprice': 241},
 {'click': 0, 'random': 300, 'zsecond payprice': 227},
 {'click': 0, 'random': 238, 'zsecond payprice': 227},
 {'click': 0, 'validation_bid': 249, 'zsecond payprice': 238},
 {'click': 0, 'validation_bid': 241, 'zsecond payprice': 241},
 {'click': 0, 'linear': 308.27, 'zsecond payprice': 300},
 {'click': 0, 'random': 300, 'zsecond payprice': 241},
 {'click': 0, 'random': 249, 'zsecond payprice': 238},
 {'click': 0, 'validation_bid': 300, 'zsecond payprice': 300},
 {'click': 0, 'linear': 308.27, 'zsecond payprice': 300},
 {'click': 0, 'validation_bid': 300, 'zsecond payprice': 238},
 {'click': 0, 'validation_bid': 300, 'zsecond payprice': 2

In [22]:
def model_evaluate(result_ls):
    dic= defaultdict(lambda:{'total_bids':0, 'total_payprice(per_imp)': 0,'click':0})
    count = Counter()
    
    i = 0
    for k1,k2,k3 in test: 
        dic[k1]['total_bids'] += 1
        dic[k1]['total_payprice(per_imp)'] += test[i][k2]/1000
        dic[k1]['click'] += test[i][k3]
        i += 1
        
    #print(test2[k1][k2])

    return dic

In [23]:
y = model_evaluate(test)
y

defaultdict(<function __main__.model_evaluate.<locals>.<lambda>>,
            {'linear': {'click': 30,
              'total_bids': 19973,
              'total_payprice(per_imp)': 5762.951000001109},
             'random': {'click': 5,
              'total_bids': 24219,
              'total_payprice(per_imp)': 5998.324999999286},
             'validation_bid': {'click': 17,
              'total_bids': 37591,
              'total_payprice(per_imp)': 9800.064699999242}})

In [ ]:
# Need to do plotting 